In [1]:

import folium
import pandas as pd
from folium.plugins import MarkerCluster, HeatMap
import geopandas as gpd
from IPython.display import IFrame
import io
from PIL import Image

In [2]:
# Load the CSV file with mobile tower data
data = pd.read_csv('mozambique_mobile_towers.csv')


In [3]:
data['Mobile'].value_counts()

UMTS    11921
GSM      5643
LTE        81
Name: Mobile, dtype: int64

In [4]:
# Filter data to keep only GSM, UMTS, and LTE mobile types
data = data[data['Mobile'].isin(['GSM', 'UMTS', 'LTE'])]


In [5]:
# Create a geopandas dataframe with the latitude and longitude columns as the geometry column
geometry = gpd.points_from_xy(data['longitude'], data['latitude'])
df = gpd.GeoDataFrame(data, geometry=geometry)


In [6]:
# Create a new column to store the buffer distance
df['buffer_distance'] = 0

# loop through each row in the dataframe
for index, row in df.iterrows():
    mobile_type = row['Mobile']
    if mobile_type == 'GSM':
        buffer_distance = 35000 # 35 kilometers in meters
    elif mobile_type == 'UMTS':
        buffer_distance = 10000 # 10 kilometers in meters
    elif mobile_type == 'LTE':
        buffer_distance = 200000 # 100 kilometers in meters
    else:
        buffer_distance = 0 # no buffer for other mobile types
    
    # create a buffer around the point using the buffer distance
    buffer = row.geometry.buffer(buffer_distance)
    
    # set the buffer as the new geometry for the row
    df.loc[index, 'geometry'] = buffer
    
    # store the buffer distance in a new column
    df.loc[index, 'buffer_distance'] = buffer_distance


In [7]:
# Create a map object
m = folium.Map(location=[data['latitude'].mean(), data['longitude'].mean()], zoom_start=10)

# Create a heatmap layer
#heatmap_data = data[['latitude', 'longitude']].values
#heatmap = HeatMap(heatmap_data, name='Heatmap',gradient={0.4: 'blue', 0.6: 'lime', 1: 'red'})

# Add the heatmap layer to the map object
#heatmap.add_to(m)

In [8]:
# Create a marker cluster layer for the mobile towers
marker_cluster = MarkerCluster(name='Mobile Towers', overlay=True, control=False)


In [9]:
# Add markers for each mobile tower to the marker cluster layer
for index, row in df.iterrows():
    marker = folium.Marker(location=[row['latitude'], row['longitude']])
    marker.add_to(marker_cluster)

# Add the marker cluster layer to the map object
marker_cluster.add_to(m)


In [10]:
m

In [12]:
# Save the map as a PNG or JPG file
m.save('mozambique_cellsites.html')  # Change the extension to '.jpg' to save as a JPG file

# Display the map in the notebook
IFrame(src='heatmap_with_markers.html', width='100%', height='700px')
